# Researching the Best Place for Urban Farming Spots in Edinburgh

This project researches the best location for urban farming in the city of Edinburgh, the capital of Scotland.

The United Kingdom has been going through [the worst economic shrink](https://www.forbes.com/sites/roberthart/2021/02/12/uk-hit-by-worst-economic-contraction-on-record-amid-covid-19-pandemic/) due to the [lockdown restrictions](https://www.cnbc.com/2021/02/22/uk-lockdown-details-and-dates-of-how-it-could-be-lifted.html) caused by the Covid-19 pandemic. [Food prices have gone up](https://www.theguardian.com/business/2021/feb/17/uk-inflation-rises-as-price-of-food-and-furniture-increases) and many people need more affordable food with constant supply. Some communities are initiating urban farming in the city of Edinburgh, the capital of Scotland,  which is also experiencing such economic condition. This project aims to find the best location for these urban farming spots.

## A Coursera and IBM Applied Data Science Capstone Project

This is the final project in the Applied Data Science Capstone course from Coursera by IBM.
This course is the last of nine in the IBM Data Science Professional Certificate path.

## Leveraging Foursquare API and clustering

This research uses Foursquare API and clustering to analyze the best area in Edinburgh to start an urban farming spot based on surrounding venues.

## Import dependencies

Before getting the data and exploring it, all the dependencies that we need are imported below.

In [ ]:
import numpy as np # library to handle data in a vectorized manner
import pandas as pd # library for data analysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import requests # library to handle requests
import json # library to handle JSON files
from pandas import json_normalize # transform JSON file into a pandas dataframe

# !conda install -c conda-forge geopy --yes # uncomment this line if you need to install geopy
# convert an address into latitude and longitude values
from geopy.geocoders import Nominatim

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans
from sklearn.datasets.samples_generator import make_blobs

# !conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you need to install folium
import folium # map rendering library

# !conda install -c conda-forge lxml --yes # uncomment this line if you need to install lxml
import lxml

print('Libraries imported.')

Libraries imported.


## 1. Get and Explore Data

In the following cells we download, clean, and wrangle the data on Edinburgh postal codes and neighborhoods.

In [ ]:
# loop the data lines
with open("EH-postcodes.csv", 'r') as temp_f:
    # get no of columns in each line
    col_count = [ len(l.split(",")) for l in temp_f.readlines() ]

# generate column names  (names will be 0, 1, 2, ..., maximum columns - 1)
column_names = [i for i in range(0, max(col_count))]

# read csv
df = pd.read_csv("EH-postcodes.csv", header=None, delimiter=",", names=column_names)

/home/jupyterlab/conda/envs/python/lib/python3.6/site-packages/IPython/core/interactiveshell.py:3072: DtypeWarning: Columns (2,3,4,5,7,17,18,19,20,21,22,25,26,27,29,32,35,36,37,40,46,47) have mixed types.Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


In [ ]:
# check out the first few lines
df.head(3)

0        1          2          3        4         5         6   \
0  Postcode  In Use?   Latitude  Longitude  Easting  Northing  Grid Ref   
1   EH1 1AA       No   55.95365  -3.188106   325910    674039  NT259740   
2   EH1 1AD      Yes  55.949135  -3.192773   325610    673542  NT256735   

       7                  8            9              10         11        12  \
0  County           District         Ward  District Code  Ward Code   Country   
1     NaN  City of Edinburgh  City Centre      S12000036  S13002929  Scotland   
2     NaN  City of Edinburgh  City Centre      S12000036  S13002929  Scotland   

            13                         14          15          16      17  \
0  County Code               Constituency  Introduced  Terminated  Parish   
1    S99999999  Edinburgh North and Leith  1980-01-01  1996-12-01     NaN   
2    S99999999             Edinburgh East  2009-06-01         NaN     NaN   

              18          19          20             21  \
0  National Park  Population  Households  Built up area   
1            NaN         NaN         NaN            NaN   
2            NaN           0           0            NaN   

                      22                                              23  \
0  Built up sub-division                   Lower layer super output area   
1                    NaN  Old Town, Princes Street and Leith Street - 03   
2                    NaN  Old Town, Princes Street and Leith Street - 01   

                 24      25        26           27         28  \
0       Rural/urban  Region  Altitude  London zone  LSOA Code   
1  Large urban area     NaN        71          NaN  S01008676   
2  Large urban area     NaN        95          NaN  S01008674   

                29         30                                         31  \
0  Local authority  MSOA Code             Middle layer super output area   
1              NaN  S02001622  Old Town, Princes Street and Leith Street   
2              NaN  S02001622  Old Town, Princes Street and Leith Street   

            32                  33                 34  \
0  Parish Code  Census output area  Constituency Code   
1          NaN           S00103339          S14000023   
2          NaN           S00103323          S14000022   

                              35       36         37            38  \
0  Index of Multiple Deprivation  Quality  User Type  Last updated   
1                           3733        8          1    2020-11-21   
2                           3481        1          0    2020-11-21   

                39                   40             41                 42  \
0  Nearest station  Distance to station  Postcode area  Postcode district   
1        Edinburgh             0.139518             EH                EH1   
2        Edinburgh             0.459657             EH                EH1   

             43              44           45              46              47  \
0  Police force   Water company    Plus Code  Average Income  Sewage Company   
1      Scotland  Scottish Water  9C7RXR36+FQ             NaN             NaN   
2      Scotland  Scottish Water  9C7RWRX4+MV             NaN             NaN   

                    48  49  50  51  52  53  
0  Travel To Work Area NaN NaN NaN NaN NaN  
1            Edinburgh NaN NaN NaN NaN NaN  
2            Edinburgh NaN NaN NaN NaN NaN

In [ ]:
# rename header with the first row
df.columns = df.iloc[0]

df.head(3)

0  Postcode  In Use?   Latitude  Longitude  Easting  Northing  Grid Ref  \
0  Postcode  In Use?   Latitude  Longitude  Easting  Northing  Grid Ref   
1   EH1 1AA       No   55.95365  -3.188106   325910    674039  NT259740   
2   EH1 1AD      Yes  55.949135  -3.192773   325610    673542  NT256735   

0  County           District         Ward  District Code  Ward Code   Country  \
0  County           District         Ward  District Code  Ward Code   Country   
1     NaN  City of Edinburgh  City Centre      S12000036  S13002929  Scotland   
2     NaN  City of Edinburgh  City Centre      S12000036  S13002929  Scotland   

0  County Code               Constituency  Introduced  Terminated  Parish  \
0  County Code               Constituency  Introduced  Terminated  Parish   
1    S99999999  Edinburgh North and Leith  1980-01-01  1996-12-01     NaN   
2    S99999999             Edinburgh East  2009-06-01         NaN     NaN   

0  National Park  Population  Households  Built up area  \
0  National Park  Population  Households  Built up area   
1            NaN         NaN         NaN            NaN   
2            NaN           0           0            NaN   

0  Built up sub-division                   Lower layer super output area  \
0  Built up sub-division                   Lower layer super output area   
1                    NaN  Old Town, Princes Street and Leith Street - 03   
2                    NaN  Old Town, Princes Street and Leith Street - 01   

0       Rural/urban  Region  Altitude  London zone  LSOA Code  \
0       Rural/urban  Region  Altitude  London zone  LSOA Code   
1  Large urban area     NaN        71          NaN  S01008676   
2  Large urban area     NaN        95          NaN  S01008674   

0  Local authority  MSOA Code             Middle layer super output area  \
0  Local authority  MSOA Code             Middle layer super output area   
1              NaN  S02001622  Old Town, Princes Street and Leith Street   
2              NaN  S02001622  Old Town, Princes Street and Leith Street   

0  Parish Code  Census output area  Constituency Code  \
0  Parish Code  Census output area  Constituency Code   
1          NaN           S00103339          S14000023   
2          NaN           S00103323          S14000022   

0  Index of Multiple Deprivation  Quality  User Type  Last updated  \
0  Index of Multiple Deprivation  Quality  User Type  Last updated   
1                           3733        8          1    2020-11-21   
2                           3481        1          0    2020-11-21   

0  Nearest station  Distance to station  Postcode area  Postcode district  \
0  Nearest station  Distance to station  Postcode area  Postcode district   
1        Edinburgh             0.139518             EH                EH1   
2        Edinburgh             0.459657             EH                EH1   

0  Police force   Water company    Plus Code  Average Income  Sewage Company  \
0  Police force   Water company    Plus Code  Average Income  Sewage Company   
1      Scotland  Scottish Water  9C7RXR36+FQ             NaN             NaN   
2      Scotland  Scottish Water  9C7RWRX4+MV             NaN             NaN   

0  Travel To Work Area  NaN  NaN  NaN  NaN  NaN  
0  Travel To Work Area  NaN  NaN  NaN  NaN  NaN  
1            Edinburgh  NaN  NaN  NaN  NaN  NaN  
2            Edinburgh  NaN  NaN  NaN  NaN  NaN

In [ ]:
# drop old header row
df.drop(df.index[0], axis=0, inplace=True)

df.head(3)

0 Postcode In Use?   Latitude  Longitude Easting Northing  Grid Ref County  \
1  EH1 1AA      No   55.95365  -3.188106  325910   674039  NT259740    NaN   
2  EH1 1AD     Yes  55.949135  -3.192773  325610   673542  NT256735    NaN   
3  EH1 1AE     Yes  55.949069  -3.189408  325820   673531  NT258735    NaN   

0           District         Ward District Code  Ward Code   Country  \
1  City of Edinburgh  City Centre     S12000036  S13002929  Scotland   
2  City of Edinburgh  City Centre     S12000036  S13002929  Scotland   
3  City of Edinburgh  City Centre     S12000036  S13002929  Scotland   

0 County Code               Constituency  Introduced  Terminated Parish  \
1   S99999999  Edinburgh North and Leith  1980-01-01  1996-12-01    NaN   
2   S99999999             Edinburgh East  2009-06-01         NaN    NaN   
3   S99999999             Edinburgh East  2018-09-01         NaN    NaN   

0 National Park Population Households Built up area Built up sub-division  \
1           NaN        NaN        NaN           NaN                   NaN   
2           NaN          0          0           NaN                   NaN   
3           NaN        NaN        NaN           NaN                   NaN   

0                   Lower layer super output area       Rural/urban Region  \
1  Old Town, Princes Street and Leith Street - 03  Large urban area    NaN   
2  Old Town, Princes Street and Leith Street - 01  Large urban area    NaN   
3  Old Town, Princes Street and Leith Street - 05  Large urban area    NaN   

0 Altitude London zone  LSOA Code Local authority  MSOA Code  \
1       71         NaN  S01008676             NaN  S02001622   
2       95         NaN  S01008674             NaN  S02001622   
3       87         NaN  S01008678             NaN  S02001622   

0             Middle layer super output area Parish Code Census output area  \
1  Old Town, Princes Street and Leith Street         NaN          S00103339   
2  Old Town, Princes Street and Leith Street         NaN          S00103323   
3  Old Town, Princes Street and Leith Street         NaN          S00103321   

0 Constituency Code Index of Multiple Deprivation Quality User Type  \
1         S14000023                          3733       8         1   
2         S14000022                          3481       1         0   
3         S14000022                          3451       1         0   

0 Last updated Nearest station Distance to station Postcode area  \
1   2020-11-21       Edinburgh            0.139518            EH   
2   2020-11-21       Edinburgh            0.459657            EH   
3   2020-11-21       Edinburgh            0.376946            EH   

0 Postcode district Police force   Water company    Plus Code Average Income  \
1               EH1     Scotland  Scottish Water  9C7RXR36+FQ            NaN   
2               EH1     Scotland  Scottish Water  9C7RWRX4+MV            NaN   
3               EH1     Scotland  Scottish Water  9C7RWRX6+J6            NaN   

0 Sewage Company Travel To Work Area  NaN  NaN  NaN  NaN  NaN  
1            NaN           Edinburgh  NaN  NaN  NaN  NaN  NaN  
2            NaN           Edinburgh  NaN  NaN  NaN  NaN  NaN  
3            NaN           Edinburgh  NaN  NaN  NaN  NaN  NaN

In [ ]:
# delete post codes not in use
# # get names of indexes for which 'In Use?' has value 'No'
code_not_in_use = df[ df['In Use?'] == 'No' ].index

# drop these row indexes from dataframe
df.drop(code_not_in_use, inplace = True)

df.head(3)

0 Postcode In Use?   Latitude  Longitude Easting Northing  Grid Ref County  \
2  EH1 1AD     Yes  55.949135  -3.192773  325610   673542  NT256735    NaN   
3  EH1 1AE     Yes  55.949069  -3.189408  325820   673531  NT258735    NaN   
9  EH1 1BB     Yes  55.952014  -3.189547  325817   673859  NT258738    NaN   

0           District         Ward District Code  Ward Code   Country  \
2  City of Edinburgh  City Centre     S12000036  S13002929  Scotland   
3  City of Edinburgh  City Centre     S12000036  S13002929  Scotland   
9  City of Edinburgh  City Centre     S12000036  S13002929  Scotland   

0 County Code    Constituency  Introduced Terminated Parish National Park  \
2   S99999999  Edinburgh East  2009-06-01        NaN    NaN           NaN   
3   S99999999  Edinburgh East  2018-09-01        NaN    NaN           NaN   
9   S99999999  Edinburgh East  1980-01-01        NaN    NaN           NaN   

0 Population Households Built up area Built up sub-division  \
2          0          0           NaN                   NaN   
3        NaN        NaN           NaN                   NaN   
9          0          0           NaN                   NaN   

0                   Lower layer super output area       Rural/urban Region  \
2  Old Town, Princes Street and Leith Street - 01  Large urban area    NaN   
3  Old Town, Princes Street and Leith Street - 05  Large urban area    NaN   
9  Old Town, Princes Street and Leith Street - 03  Large urban area    NaN   

0 Altitude London zone  LSOA Code Local authority  MSOA Code  \
2       95         NaN  S01008674             NaN  S02001622   
3       87         NaN  S01008678             NaN  S02001622   
9       63         NaN  S01008676             NaN  S02001622   

0             Middle layer super output area Parish Code Census output area  \
2  Old Town, Princes Street and Leith Street         NaN          S00103323   
3  Old Town, Princes Street and Leith Street         NaN          S00103321   
9  Old Town, Princes Street and Leith Street         NaN          S00103339   

0 Constituency Code Index of Multiple Deprivation Quality User Type  \
2         S14000022                          3481       1         0   
3         S14000022                          3451       1         0   
9         S14000022                          3733       1         0   

0 Last updated Nearest station Distance to station Postcode area  \
2   2020-11-21       Edinburgh            0.459657            EH   
3   2020-11-21       Edinburgh            0.376946            EH   
9   2020-11-21       Edinburgh           0.0923916            EH   

0 Postcode district Police force   Water company    Plus Code Average Income  \
2               EH1     Scotland  Scottish Water  9C7RWRX4+MV            NaN   
3               EH1     Scotland  Scottish Water  9C7RWRX6+J6            NaN   
9               EH1     Scotland  Scottish Water  9C7RXR26+R5            NaN   

0 Sewage Company Travel To Work Area  NaN  NaN  NaN  NaN  NaN  
2            NaN           Edinburgh  NaN  NaN  NaN  NaN  NaN  
3            NaN           Edinburgh  NaN  NaN  NaN  NaN  NaN  
9            NaN           Edinburgh  NaN  NaN  NaN  NaN  NaN

In [ ]:
# create a new dataframe with only necessary columns
df_edinburgh = df[['Postcode', 'Latitude', 'Longitude', 'District', 'Ward', 'Constituency', 'Rural/urban', 'Lower layer super output area', 'Middle layer super output area']]

df_edinburgh.head(3)

0 Postcode   Latitude  Longitude           District         Ward  \
2  EH1 1AD  55.949135  -3.192773  City of Edinburgh  City Centre   
3  EH1 1AE  55.949069  -3.189408  City of Edinburgh  City Centre   
9  EH1 1BB  55.952014  -3.189547  City of Edinburgh  City Centre   

0    Constituency       Rural/urban  \
2  Edinburgh East  Large urban area   
3  Edinburgh East  Large urban area   
9  Edinburgh East  Large urban area   

0                   Lower layer super output area  \
2  Old Town, Princes Street and Leith Street - 01   
3  Old Town, Princes Street and Leith Street - 05   
9  Old Town, Princes Street and Leith Street - 03   

0             Middle layer super output area  
2  Old Town, Princes Street and Leith Street  
3  Old Town, Princes Street and Leith Street  
9  Old Town, Princes Street and Leith Street

In [ ]:
# check the last columns
df_edinburgh.tail(3)

0      Postcode Latitude Longitude           District  \
32454  EH95 1AH  55.9786  -3.25352  City of Edinburgh   
32455  EH99 1SP  55.9521  -3.17459  City of Edinburgh   
32457  EH99 1YB  55.9432  -3.23295  City of Edinburgh   

0                          Ward               Constituency       Rural/urban  \
32454                     Forth  Edinburgh North and Leith  Large urban area   
32455               City Centre             Edinburgh East  Large urban area   
32457  Corstorphine/Murrayfield             Edinburgh West  Large urban area   

0                  Lower layer super output area  \
32454             Granton West and Salvesen - 05   
32455  Canongate, Southside and Dumbiedykes - 05   
32457                         Deans Village - 07   

0            Middle layer super output area  
32454             Granton West and Salvesen  
32455  Canongate, Southside and Dumbiedykes  
32457                         Deans Village

In [ ]:
# count missing values
print(" \nCount total NaN at each column in the dataframe : \n\n",
      df_edinburgh.isnull().sum())

 
Count total NaN at each column in the dataframe : 

 0
Postcode                           0
Latitude                           0
Longitude                          0
District                          10
Ward                              10
Constituency                      10
Rural/urban                       10
Lower layer super output area     10
Middle layer super output area    10
dtype: int64


In [ ]:
# drop rows with missing values
df_edinburgh.dropna(axis=0, how='any', inplace=False)
df_edinburgh.head(3)

0 Postcode   Latitude  Longitude           District         Ward  \
2  EH1 1AD  55.949135  -3.192773  City of Edinburgh  City Centre   
3  EH1 1AE  55.949069  -3.189408  City of Edinburgh  City Centre   
9  EH1 1BB  55.952014  -3.189547  City of Edinburgh  City Centre   

0    Constituency       Rural/urban  \
2  Edinburgh East  Large urban area   
3  Edinburgh East  Large urban area   
9  Edinburgh East  Large urban area   

0                   Lower layer super output area  \
2  Old Town, Princes Street and Leith Street - 01   
3  Old Town, Princes Street and Leith Street - 05   
9  Old Town, Princes Street and Leith Street - 03   

0             Middle layer super output area  
2  Old Town, Princes Street and Leith Street  
3  Old Town, Princes Street and Leith Street  
9  Old Town, Princes Street and Leith Street

In [ ]:
# check dataframe size
df_edinburgh.shape

(24476, 9)

Since the urban farming spots are planned to be in Edinburgh city centre, we are going to only work with area with postcodes starting with EH1

In [ ]:
# filter all rows for which the ward is City Centre
edinburgh_data = df_edinburgh[df_edinburgh['Postcode'].str.contains('EH1 ')]

In [ ]:
# check the shape of the new dataframe
edinburgh_data.shape

(325, 9)

In [ ]:
# ensure latitude and longitude are of float type
edinburgh_data.loc[:, ('Latitude', 'Longitude')] = edinburgh_data.loc[:, ('Latitude', 'Longitude')].apply(pd.to_numeric)

/home/jupyterlab/conda/envs/python/lib/python3.6/site-packages/pandas/core/indexing.py:670: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  iloc._setitem_with_indexer(indexer, value)
/home/jupyterlab/conda/envs/python/lib/python3.6/site-packages/ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  


In [ ]:
# check the new dataframe
edinburgh_data.head(3)

0 Postcode Latitude Longitude           District         Ward    Constituency  \
2  EH1 1AD  55.9491  -3.19277  City of Edinburgh  City Centre  Edinburgh East   
3  EH1 1AE  55.9491  -3.18941  City of Edinburgh  City Centre  Edinburgh East   
9  EH1 1BB   55.952  -3.18955  City of Edinburgh  City Centre  Edinburgh East   

0       Rural/urban                   Lower layer super output area  \
2  Large urban area  Old Town, Princes Street and Leith Street - 01   
3  Large urban area  Old Town, Princes Street and Leith Street - 05   
9  Large urban area  Old Town, Princes Street and Leith Street - 03   

0             Middle layer super output area  
2  Old Town, Princes Street and Leith Street  
3  Old Town, Princes Street and Leith Street  
9  Old Town, Princes Street and Leith Street

In [ ]:
# reset the dataframe index
edinburgh_data.reset_index(drop=True, inplace=True)

edinburgh_data.head(3)

0 Postcode Latitude Longitude           District         Ward    Constituency  \
0  EH1 1AD  55.9491  -3.19277  City of Edinburgh  City Centre  Edinburgh East   
1  EH1 1AE  55.9491  -3.18941  City of Edinburgh  City Centre  Edinburgh East   
2  EH1 1BB   55.952  -3.18955  City of Edinburgh  City Centre  Edinburgh East   

0       Rural/urban                   Lower layer super output area  \
0  Large urban area  Old Town, Princes Street and Leith Street - 01   
1  Large urban area  Old Town, Princes Street and Leith Street - 05   
2  Large urban area  Old Town, Princes Street and Leith Street - 03   

0             Middle layer super output area  
0  Old Town, Princes Street and Leith Street  
1  Old Town, Princes Street and Leith Street  
2  Old Town, Princes Street and Leith Street

In order to define an instance of the geocoder, we need to define a user_agent. We name our agent to_explorer, as shown below.

In [ ]:
address = 'Edinburgh, Scotland, United Kingdom'

geolocator = Nominatim(user_agent="to_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geographical coordinates of Edinburgh, Scotland, United Kingdom are {}, {}.'.format(latitude, longitude))

The geographical coordinates of Edinburgh, Scotland, United Kingdom are 55.9533456, -3.1883749.


### Create a map of Edinburgh with neighborhoods superimposed on top

In [ ]:
# create a map of Edinburgh using latitude and longitude values
map_edinburgh = folium.Map(location=[latitude, longitude], zoom_start=15)

# add markers to the map
for postcode, lat, lng, ward, constituency, area in zip(edinburgh_data['Postcode'], edinburgh_data['Latitude'], edinburgh_data['Longitude'], edinburgh_data['Ward'], edinburgh_data['Constituency'], edinburgh_data['Middle layer super output area']):
    label = '{}, {}, {}, {}'.format(postcode, area, constituency, ward)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='cadetblue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_edinburgh)

map_edinburgh

### Define Foursquare Credentials and Version
Here, we are going to start utilizing the Foursquare API to explore the neighborhoods and segment them.

In [ ]:
# details for Foursquare API calls
CLIENT_ID =  # Enter Foursquare ID
CLIENT_SECRET =  # Enter Foursquare Secret
VERSION = '20210301' # Foursquare API version

print('Credentials:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

### Explore the first postcode area in our dataframe.

Get the postcode and area's name.

In [ ]:
print("The first postcode and area is " + edinburgh_data.loc[0, 'Postcode'] + ", " + edinburgh_data.loc[0, 'Middle layer super output area'])

The first postcode and area is EH1 1AD, Old Town, Princes Street and Leith Street


Get the postcode area's latitude and longitude values.

In [ ]:
postcode_latitude = edinburgh_data.loc[0, 'Latitude'] # postcode latitude value
postcode_longitude = edinburgh_data.loc[0, 'Longitude'] # postcode longitude value

postcode_name = edinburgh_data.loc[0, 'Postcode'] # postcode name

print('Latitude and longitude values of {} are {}, {}.'.format(postcode_name,
                                                               postcode_latitude,
                                                               postcode_longitude))

Latitude and longitude values of EH1 1AD are 55.949135, -3.192773.


### Get the top 50 venues that are in the first neighborhood within a radius of 300 meters.

First, we create the GET request URL.

In [ ]:
LIMIT = 50 # limit the number of venues returned by Foursquare API
radius = 250 # define radius
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID,
    CLIENT_SECRET,
    VERSION,
    postcode_latitude,
    postcode_longitude,
    radius,
    LIMIT)
url # display URL

'https://api.foursquare.com/v2/venues/explore?&client_id=TC0PQVXTVXDKVV22JU3GSJQIO3YQQIXWYZ1LB53OD5Q4EWOP&client_secret=0PDPFKTT0FK1BULZFS3DS2SLBA4FZ41A3KRWCQR50WOHTSLE&v=20210301&ll=55.949135,-3.192773&radius=250&limit=50'

Next, we send the GET request and examine the results.

In [ ]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '603f38ff2c188b2f80351433'},
 'response': {'suggestedFilters': {'header': 'Tap to show:',
   'filters': [{'name': 'Open now', 'key': 'openNow'}]},
  'headerLocation': 'Old Town',
  'headerFullLocation': 'Old Town, Edinburgh',
  'headerLocationGranularity': 'neighborhood',
  'totalResults': 55,
  'suggestedBounds': {'ne': {'lat': 55.95138500225,
    'lng': -3.1887621297672593},
   'sw': {'lat': 55.94688499775, 'lng': -3.1967838702327405}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '4dc6f4871f6ef43b8a3b8d61',
       'name': 'Old Town',
       'location': {'lat': 55.94950019084528,
        'lng': -3.192805051803589,
        'labeledLatLngs': [{'label': 'display',
          'lat': 55.94950019084528,
          'lng': -3.192805051803589

In the Foursquare data, all information is in the items key. Before we proceed, we get the get_category_type function from the Foursquare lab.

In [ ]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']

    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

Then, we clean the json and structure it into a pandas dataframe.

In [ ]:
venues = results['response']['groups'][0]['items']

# flatten JSON
nearby_venues = json_normalize(venues)

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues = nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

name    categories        lat       lng
0              Old Town  Neighborhood  55.949500 -3.192805
1           The Milkman   Coffee Shop  55.950650 -3.191010
2          La Barantine          Café  55.948362 -3.194388
3  St. Giles' Cathedral        Church  55.949494 -3.190852
4     BrewDog Edinburgh      Beer Bar  55.948507 -3.189626

Let's check how many venues were returned by Foursquare.

In [ ]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

50 venues were returned by Foursquare.


## 2. Explore Areas in Edinburgh

We create a function to repeat the same process on all the neighborhoods.

In [ ]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):

    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)

        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID,
            CLIENT_SECRET,
            VERSION,
            lat,
            lng,
            radius,
            LIMIT)

        # make the GET request

        results = requests.get(url).json()['response']['groups'][0]['items']

        # return only relevant information for each nearby venue
        venues_list.append([(
            name,
            lat,
            lng,
            v['venue']['name'],
            v['venue']['location']['lat'],
            v['venue']['location']['lng'],
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Postcode',
                  'Postcode Latitude',
                  'Postcode Longitude',
                  'Venue',
                  'Venue Latitude',
                  'Venue Longitude',
                  'Venue Category']

    return(nearby_venues)

Now we run the above function on each neighborhood and save it in a new dataframe called edinburgh_venues.

In [ ]:
edinburgh_venues = getNearbyVenues(names = edinburgh_data['Postcode'],
                                 latitudes = edinburgh_data['Latitude'],
                                 longitudes = edinburgh_data['Longitude']
                                )

EH1 1AD
EH1 1AE
EH1 1BB
EH1 1BE
EH1 1BL
EH1 1BN
EH1 1BP
EH1 1BQ
EH1 1BS
EH1 1BU
EH1 1BX
EH1 1DD
EH1 1DE
EH1 1DF
EH1 1DH
EH1 1DR
EH1 1DT
EH1 1DY
EH1 1EE
EH1 1EG
EH1 1EJ
EH1 1EL
EH1 1EN
EH1 1ES
EH1 1EY
EH1 1EZ
EH1 1HA
EH1 1HB
EH1 1HD
EH1 1HE
EH1 1HJ
EH1 1HN
EH1 1HR
EH1 1HT
EH1 1HU
EH1 1JF
EH1 1JG
EH1 1JH
EH1 1JJ
EH1 1JN
EH1 1JQ
EH1 1JR
EH1 1JS
EH1 1JT
EH1 1JU
EH1 1JW
EH1 1JX
EH1 1JY
EH1 1JZ
EH1 1LA
EH1 1LB
EH1 1LD
EH1 1LG
EH1 1LL
EH1 1LS
EH1 1LT
EH1 1LU
EH1 1LW
EH1 1LY
EH1 1LZ
EH1 1NA
EH1 1NB
EH1 1ND
EH1 1NE
EH1 1NL
EH1 1NP
EH1 1NQ
EH1 1NS
EH1 1NU
EH1 1NW
EH1 1NY
EH1 1PB
EH1 1PD
EH1 1PE
EH1 1PG
EH1 1PL
EH1 1PN
EH1 1PQ
EH1 1PS
EH1 1PT
EH1 1PW
EH1 1PX
EH1 1PZ
EH1 1QA
EH1 1QB
EH1 1QG
EH1 1QL
EH1 1QN
EH1 1QQ
EH1 1QR
EH1 1QS
EH1 1QT
EH1 1QU
EH1 1QW
EH1 1QX
EH1 1QY
EH1 1RB
EH1 1RD
EH1 1RE
EH1 1RF
EH1 1RN
EH1 1RP
EH1 1RQ
EH1 1RR
EH1 1RT
EH1 1RW
EH1 1RZ
EH1 1SB
EH1 1SD
EH1 1SG
EH1 1SJ
EH1 1SP
EH1 1SR
EH1 1SS
EH1 1SU
EH1 1SW
EH1 1SX
EH1 1SY
EH1 1TA
EH1 1TB
EH1 1TD
EH1 1TE
EH1 1TF
EH1 1TG
EH1 1TH


In [ ]:
# check the results
print(edinburgh_venues.shape)
edinburgh_venues.head()

(14825, 7)


Postcode  Postcode Latitude  Postcode Longitude                 Venue  \
0  EH1 1AD          55.949135           -3.192773              Old Town   
1  EH1 1AD          55.949135           -3.192773           The Milkman   
2  EH1 1AD          55.949135           -3.192773     BrewDog Edinburgh   
3  EH1 1AD          55.949135           -3.192773          La Barantine   
4  EH1 1AD          55.949135           -3.192773  St. Giles' Cathedral   

   Venue Latitude  Venue Longitude Venue Category  
0       55.949500        -3.192805   Neighborhood  
1       55.950650        -3.191010    Coffee Shop  
2       55.948507        -3.189626       Beer Bar  
3       55.948362        -3.194388           Café  
4       55.949494        -3.190852         Church

Let's check how many venues were returned for each neighborhood.

In [ ]:
edinburgh_venues.groupby('Postcode').count()

Postcode Latitude  Postcode Longitude  Venue  Venue Latitude  \
Postcode                                                                 
EH1 1AD                  50                  50     50              50   
EH1 1AE                  50                  50     50              50   
EH1 1BB                  50                  50     50              50   
EH1 1BE                  50                  50     50              50   
EH1 1BL                  50                  50     50              50   
EH1 1BN                  50                  50     50              50   
EH1 1BP                  50                  50     50              50   
EH1 1BQ                  50                  50     50              50   
EH1 1BS                  50                  50     50              50   
EH1 1BU                  50                  50     50              50   
EH1 1BX                  50                  50     50              50   
EH1 1DD                  50                  50     50              50   
EH1 1DE                  50                  50     50              50   
EH1 1DF                  50                  50     50              50   
EH1 1DH                  50                  50     50              50   
EH1 1DR                  50                  50     50              50   
EH1 1DT                  50                  50     50              50   
EH1 1DY                  50                  50     50              50   
EH1 1EE                  50                  50     50              50   
EH1 1EG                  50                  50     50              50   
EH1 1EJ                  50                  50     50              50   
EH1 1EL                  50                  50     50              50   
EH1 1EN                  50                  50     50              50   
EH1 1ES                  50                  50     50              50   
EH1 1EY                  50                  50     50              50   
EH1 1EZ                  50                  50     50              50   
EH1 1HA                  50                  50     50              50   
EH1 1HB                  50                  50     50              50   
EH1 1HD                  50                  50     50              50   
EH1 1HE                  50                  50     50              50   
EH1 1HJ                  50                  50     50              50   
EH1 1HN                  50                  50     50              50   
EH1 1HR                  50                  50     50              50   
EH1 1HT                  50                  50     50              50   
EH1 1HU                  50                  50     50              50   
EH1 1JF                  50                  50     50              50   
EH1 1JG                  50                  50     50              50   
EH1 1JH                  50                  50     50              50   
EH1 1JJ                  50                  50     50              50   
EH1 1JN                  50                  50     50              50   
EH1 1JQ                  50                  50     50              50   
EH1 1JR                  50                  50     50              50   
EH1 1JS                  50                  50     50              50   
EH1 1JT                  50                  50     50              50   
EH1 1JU                  50                  50     50              50   
EH1 1JW                  50                  50     50              50   
EH1 1JX                  50                  50     50              50   
EH1 1JY                  50                  50     50              50   
EH1 1JZ                  50                  50     50              50   
EH1 1LA                  50                  50     50              50   
EH1 1LB                  50                  50     50              50   
EH1 1LD                  50                  50     50              50   
EH1 1LG       

Let's find out how many unique categories can be curated from all of the returned venues.

In [ ]:
print('There are {} uniques categories.'.format(len(edinburgh_venues['Venue Category'].unique())))

There are 123 uniques categories.


## 3. Analyze Each Neighborhood

We analyze how many of each type of venues there are in each neighborhood.

In [ ]:
# perform one hot encoding
edinburgh_onehot = pd.get_dummies(edinburgh_venues[['Venue Category']], prefix="", prefix_sep="")

edinburgh_onehot.head()

African Restaurant  American Restaurant  Argentinian Restaurant  \
0                   0                    0                       0   
1                   0                    0                       0   
2                   0                    0                       0   
3                   0                    0                       0   
4                   0                    0                       0   

   Art Gallery  Art Museum  Asian Restaurant  Auto Garage  Bakery  Bar  \
0            0           0                 0            0       0    0   
1            0           0                 0            0       0    0   
2            0           0                 0            0       0    0   
3            0           0                 0            0       0    0   
4            0           0                 0            0       0    0   

   Beer Bar  Bistro  Bookstore  Boutique  Bowling Green  Breakfast Spot  \
0         0       0          0         0              0               0   
1         0       0          0         0              0               0   
2         1       0          0         0              0               0   
3         0       0          0         0              0               0   
4         0       0          0         0              0               0   

   Burger Joint  Butcher  Café  Candy Store  Castle  Chinese Restaurant  \
0             0        0     0            0       0                   0   
1             0        0     0            0       0                   0   
2             0        0     0            0       0                   0   
3             0        0     1            0       0                   0   
4             0        0     0            0       0                   0   

   Chocolate Shop  Church  Cocktail Bar  Coffee Shop  Comedy Club  \
0               0       0             0            0            0   
1               0       0             0            1            0   
2               0       0             0            0            0   
3               0       0             0            0            0   
4               0       1             0            0            0   

   Concert Hall  Cosmetics Shop  Creperie  Cupcake Shop  Dance Studio  \
0             0               0         0             0             0   
1             0               0         0             0             0   
2             0               0         0             0             0   
3             0               0         0             0             0   
4             0               0         0             0             0   

   Deli / Bodega  Dessert Shop  Eastern European Restaurant  \
0              0             0                            0   
1              0             0                            0   
2              0             0                            0   
3              0             0                            0   
4              0             0                            0   

   Electronics Store  English Restaurant  Escape Room  Event Service  \
0                  0                   0            0              0   
1                  0                   0            0              0   
2                  0                   0            0              0   
3                  0                   0            0              0   
4                  0                   0            0              0   

   Farmers Market  Fast Food Restaurant  Fountain  French Restaurant  Garden  \
0               0                     0         0                  0       0   
1               0                     0         0                  0       0   
2               0                     0         0                  0       0   
3               0                     0         0                  0       0   
4               0                     0         0                  0       0   

   Gastropub  Gelato Shop  General College & University  Gift Shop  \
0          0      

In [ ]:
# add postcode column back to dataframe
edinburgh_onehot['Postcode'] = edinburgh_venues['Postcode']

edinburgh_onehot.head()

African Restaurant  American Restaurant  Argentinian Restaurant  \
0                   0                    0                       0   
1                   0                    0                       0   
2                   0                    0                       0   
3                   0                    0                       0   
4                   0                    0                       0   

   Art Gallery  Art Museum  Asian Restaurant  Auto Garage  Bakery  Bar  \
0            0           0                 0            0       0    0   
1            0           0                 0            0       0    0   
2            0           0                 0            0       0    0   
3            0           0                 0            0       0    0   
4            0           0                 0            0       0    0   

   Beer Bar  Bistro  Bookstore  Boutique  Bowling Green  Breakfast Spot  \
0         0       0          0         0              0               0   
1         0       0          0         0              0               0   
2         1       0          0         0              0               0   
3         0       0          0         0              0               0   
4         0       0          0         0              0               0   

   Burger Joint  Butcher  Café  Candy Store  Castle  Chinese Restaurant  \
0             0        0     0            0       0                   0   
1             0        0     0            0       0                   0   
2             0        0     0            0       0                   0   
3             0        0     1            0       0                   0   
4             0        0     0            0       0                   0   

   Chocolate Shop  Church  Cocktail Bar  Coffee Shop  Comedy Club  \
0               0       0             0            0            0   
1               0       0             0            1            0   
2               0       0             0            0            0   
3               0       0             0            0            0   
4               0       1             0            0            0   

   Concert Hall  Cosmetics Shop  Creperie  Cupcake Shop  Dance Studio  \
0             0               0         0             0             0   
1             0               0         0             0             0   
2             0               0         0             0             0   
3             0               0         0             0             0   
4             0               0         0             0             0   

   Deli / Bodega  Dessert Shop  Eastern European Restaurant  \
0              0             0                            0   
1              0             0                            0   
2              0             0                            0   
3              0             0                            0   
4              0             0                            0   

   Electronics Store  English Restaurant  Escape Room  Event Service  \
0                  0                   0            0              0   
1                  0                   0            0              0   
2                  0                   0            0              0   
3                  0                   0            0              0   
4                  0                   0            0              0   

   Farmers Market  Fast Food Restaurant  Fountain  French Restaurant  Garden  \
0               0                     0         0                  0       0   
1               0                     0         0                  0       0   
2               0                     0         0                  0       0   
3               0                     0         0                  0       0   
4               0                     0         0                  0       0   

   Gastropub  Gelato Shop  General College & University  Gift Shop  \
0          0      

In [ ]:
# move postcode column to the first column
postcode = edinburgh_onehot.pop('Postcode')
edinburgh_onehot.insert(0, 'Postcode', postcode)

edinburgh_onehot.head()

Postcode  African Restaurant  American Restaurant  Argentinian Restaurant  \
0  EH1 1AD                   0                    0                       0   
1  EH1 1AD                   0                    0                       0   
2  EH1 1AD                   0                    0                       0   
3  EH1 1AD                   0                    0                       0   
4  EH1 1AD                   0                    0                       0   

   Art Gallery  Art Museum  Asian Restaurant  Auto Garage  Bakery  Bar  \
0            0           0                 0            0       0    0   
1            0           0                 0            0       0    0   
2            0           0                 0            0       0    0   
3            0           0                 0            0       0    0   
4            0           0                 0            0       0    0   

   Beer Bar  Bistro  Bookstore  Boutique  Bowling Green  Breakfast Spot  \
0         0       0          0         0              0               0   
1         0       0          0         0              0               0   
2         1       0          0         0              0               0   
3         0       0          0         0              0               0   
4         0       0          0         0              0               0   

   Burger Joint  Butcher  Café  Candy Store  Castle  Chinese Restaurant  \
0             0        0     0            0       0                   0   
1             0        0     0            0       0                   0   
2             0        0     0            0       0                   0   
3             0        0     1            0       0                   0   
4             0        0     0            0       0                   0   

   Chocolate Shop  Church  Cocktail Bar  Coffee Shop  Comedy Club  \
0               0       0             0            0            0   
1               0       0             0            1            0   
2               0       0             0            0            0   
3               0       0             0            0            0   
4               0       1             0            0            0   

   Concert Hall  Cosmetics Shop  Creperie  Cupcake Shop  Dance Studio  \
0             0               0         0             0             0   
1             0               0         0             0             0   
2             0               0         0             0             0   
3             0               0         0             0             0   
4             0               0         0             0             0   

   Deli / Bodega  Dessert Shop  Eastern European Restaurant  \
0              0             0                            0   
1              0             0                            0   
2              0             0                            0   
3              0             0                            0   
4              0             0                            0   

   Electronics Store  English Restaurant  Escape Room  Event Service  \
0                  0                   0            0              0   
1                  0                   0            0              0   
2                  0                   0            0              0   
3                  0                   0            0              0   
4                  0                   0            0              0   

   Farmers Market  Fast Food Restaurant  Fountain  French Restaurant  Garden  \
0               0                     0         0                  0       0   
1               0                     0         0                  0       0   
2               0                     0         0                  0       0   
3               0                     0         0                  0       0   
4               0                     0         0                  0       0   

   Gastropub  Gelato Shop  Genera

We examine the new dataframe size.

In [ ]:
edinburgh_onehot.shape

(14825, 124)

Next, we group rows by postcode and by taking the mean of the frequency of occurrence of each category.

In [ ]:
edinburgh_grouped = edinburgh_onehot.groupby('Postcode').mean().reset_index()
edinburgh_grouped

Postcode  African Restaurant  American Restaurant  Argentinian Restaurant  \
0    EH1 1AD            0.000000             0.000000                0.000000   
1    EH1 1AE            0.000000             0.000000                0.000000   
2    EH1 1BB            0.000000             0.000000                0.000000   
3    EH1 1BE            0.000000             0.000000                0.000000   
4    EH1 1BL            0.000000             0.000000                0.000000   
5    EH1 1BN            0.000000             0.000000                0.000000   
6    EH1 1BP            0.000000             0.000000                0.000000   
7    EH1 1BQ            0.000000             0.000000                0.020000   
8    EH1 1BS            0.000000             0.000000                0.000000   
9    EH1 1BU            0.000000             0.000000                0.000000   
10   EH1 1BX            0.000000             0.000000                0.000000   
11   EH1 1DD            0.000000             0.000000                0.000000   
12   EH1 1DE            0.000000             0.000000                0.000000   
13   EH1 1DF            0.000000             0.000000                0.000000   
14   EH1 1DH            0.000000             0.000000                0.000000   
15   EH1 1DR            0.000000             0.000000                0.000000   
16   EH1 1DT            0.000000             0.000000                0.000000   
17   EH1 1DY            0.000000             0.000000                0.000000   
18   EH1 1EE            0.000000             0.000000                0.000000   
19   EH1 1EG            0.000000             0.000000                0.000000   
20   EH1 1EJ            0.000000             0.000000                0.000000   
21   EH1 1EL            0.000000             0.000000                0.000000   
22   EH1 1EN            0.000000             0.000000                0.000000   
23   EH1 1ES            0.000000             0.000000                0.000000   
24   EH1 1EY            0.020000             0.000000                0.000000   
25   EH1 1EZ            0.020000             0.000000                0.000000   
26   EH1 1HA            0.020000             0.000000                0.000000   
27   EH1 1HB            0.020000             0.000000                0.000000   
28   EH1 1HD            0.020000             0.000000                0.000000   
29   EH1 1HE            0.020000             0.000000                0.000000   
30   EH1 1HJ            0.000000             0.000000                0.000000   
31   EH1 1HN            0.000000             0.000000                0.000000   
32   EH1 1HR            0.020000             0.000000                0.000000   
33   EH1 1HT            0.000000             0.000000                0.000000   
34   EH1 1HU            0.000000             0.000000                0.000000   
35   EH1 1JF            0.020000             0.000000                0.000000   
36   EH1 1JG            0.000000             0.000000                0.000000   
37   EH1 1JH            0.000000             0.000000                0.000000   
38   EH1 1JJ            0.000000             0.000000                0.000000   
39   EH1 1JN            0.000000             0.000000                0.000000   
40   EH1 1JQ            0.000000             0.000000                0.000000   
41   EH1 1JR            0.000000             0.000000                0.000000   
42   EH1 1JS            0.000000             0.000000                0.000000   
43   EH1 1JT            0.000000             0.000000                0.000000   
44   EH1 1JU            0.000000             0.000000                0.000000   
45   EH1 1JW            0.000000             0.000000                0.000000   
46   EH1 1JX            0.000000             0.000000                0.000000   
47   EH1 1JY            0.000000             0.000000                0.000000   
48   EH1 1JZ            0.000000   

We confirm the new size.

In [ ]:
edinburgh_grouped.shape

(325, 124)

We print each postcode along with the top five most common venues.

In [ ]:
num_top_venues = 5

for code in edinburgh_grouped['Postcode']:
    print("---- " + code + " ----")
    temp = edinburgh_grouped[edinburgh_grouped['Postcode'] == code].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

---- EH1 1AD ----
            venue  freq
0            Café  0.08
1           Hotel  0.06
2  Scenic Lookout  0.06
3      Restaurant  0.06
4             Pub  0.06


---- EH1 1AE ----
    venue  freq
0   Hotel  0.08
1  Museum  0.08
2    Café  0.08
3     Pub  0.04
4     Bar  0.04


---- EH1 1BB ----
                 venue  freq
0                Hotel  0.14
1           Whisky Bar  0.06
2                  Bar  0.06
3           Restaurant  0.06
4  Scottish Restaurant  0.04


---- EH1 1BE ----
                 venue  freq
0                Hotel  0.14
1                  Bar  0.08
2           Whisky Bar  0.06
3  Scottish Restaurant  0.04
4             Beer Bar  0.04


---- EH1 1BL ----
        venue  freq
0       Hotel  0.10
1         Pub  0.08
2        Café  0.08
3  Whisky Bar  0.06
4  Restaurant  0.06


---- EH1 1BN ----
        venue  freq
0       Hotel  0.12
1        Café  0.08
2  Restaurant  0.06
3  Whisky Bar  0.06
4         Pub  0.06


---- EH1 1BP ----
        venue  freq
0       Hotel 

**We put that into a pandas dataframe**

First, we write a function to sort the venues in descending order.

In [ ]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)

    return row_categories_sorted.index.values[0:num_top_venues]

Next, we create the new dataframe and display the top 10 venues for each postcode.

In [ ]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Postcode']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Postcode'] = edinburgh_grouped['Postcode']

for ind in np.arange(edinburgh_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(edinburgh_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Postcode 1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0  EH1 1AD                  Café            Restaurant                   Pub   
1  EH1 1AE                Museum                  Café                 Hotel   
2  EH1 1BB                 Hotel                   Bar            Whisky Bar   
3  EH1 1BE                 Hotel                   Bar            Whisky Bar   
4  EH1 1BL                 Hotel                  Café                   Pub   

  4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0        Scenic Lookout                 Hotel                Museum   
1            Whisky Bar            Restaurant                   Bar   
2            Restaurant         Tour Provider              Beer Bar   
3   Scottish Restaurant         Tour Provider                   Pub   
4            Whisky Bar            Restaurant                   Bar   

  7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
0            Whisky Bar   Scottish Restaurant    Seafood Restaurant   
1              Beer Bar                   Pub           Coffee Shop   
2   Scottish Restaurant                   Pub             Gastropub   
3              Beer Bar           Wings Joint                   Gym   
4   Scottish Restaurant           Wings Joint                  Park   

  10th Most Common Venue  
0              Juice Bar  
1              Gastropub  
2      Outdoor Sculpture  
3                 Church  
4         Scenic Lookout

## 4. Cluster Neighborhoods

We run k-means clustering to cluster the neighborhoods into 5 clusters.

In [ ]:
kclusters = 5

edinburgh_grouped_clustering = edinburgh_grouped.drop('Postcode', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(edinburgh_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([0, 2, 2, 2, 2, 2, 2, 2, 2, 2], dtype=int32)

We create a new dataframe that includes the cluster as well as the top 10 venues for each postcode.

In [ ]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

In [ ]:
edinburgh_merged = edinburgh_data

# merge edinburgh_grouped with edinburgh_data to add latitude/longitude for each neighborhood
edinburgh_merged = edinburgh_merged.join(neighborhoods_venues_sorted.set_index('Postcode'), on='Postcode')

# check the first columns!
edinburgh_merged.head()

Postcode Latitude Longitude           District         Ward    Constituency  \
0  EH1 1AD  55.9491  -3.19277  City of Edinburgh  City Centre  Edinburgh East   
1  EH1 1AE  55.9491  -3.18941  City of Edinburgh  City Centre  Edinburgh East   
2  EH1 1BB   55.952  -3.18955  City of Edinburgh  City Centre  Edinburgh East   
3  EH1 1BE   55.952  -3.18994  City of Edinburgh  City Centre  Edinburgh East   
4  EH1 1BL  55.9507  -3.19173  City of Edinburgh  City Centre  Edinburgh East   

        Rural/urban                   Lower layer super output area  \
0  Large urban area  Old Town, Princes Street and Leith Street - 01   
1  Large urban area  Old Town, Princes Street and Leith Street - 05   
2  Large urban area  Old Town, Princes Street and Leith Street - 03   
3  Large urban area  Old Town, Princes Street and Leith Street - 03   
4  Large urban area  Old Town, Princes Street and Leith Street - 04   

              Middle layer super output area  Cluster Labels  \
0  Old Town, Princes Street and Leith Street               0   
1  Old Town, Princes Street and Leith Street               2   
2  Old Town, Princes Street and Leith Street               2   
3  Old Town, Princes Street and Leith Street               2   
4  Old Town, Princes Street and Leith Street               2   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0                  Café            Restaurant                   Pub   
1                Museum                  Café                 Hotel   
2                 Hotel                   Bar            Whisky Bar   
3                 Hotel                   Bar            Whisky Bar   
4                 Hotel                  Café                   Pub   

  4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0        Scenic Lookout                 Hotel                Museum   
1            Whisky Bar            Restaurant                   Bar   
2            Restaurant         Tour Provider              Beer Bar   
3   Scottish Restaurant         Tour Provider                   Pub   
4            Whisky Bar            Restaurant                   Bar   

  7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
0            Whisky Bar   Scottish Restaurant    Seafood Restaurant   
1              Beer Bar                   Pub           Coffee Shop   
2   Scottish Restaurant                   Pub             Gastropub   
3              Beer Bar           Wings Joint                   Gym   
4   Scottish Restaurant           Wings Joint                  Park   

  10th Most Common Venue  
0              Juice Bar  
1              Gastropub  
2      Outdoor Sculpture  
3                 Church  
4         Scenic Lookout

Finally, we visualize the resulting clusters.

In [ ]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=15)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(edinburgh_merged['Latitude'], edinburgh_merged['Longitude'], edinburgh_merged['Postcode'], edinburgh_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        #color=rainbow[cluster-1],
        fill=True,
        #fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)

map_clusters

## 5. Examine Clusters

Now, we can examine each cluster and determine the discriminating venue categories that distinguish each cluster. Based on the defining categories, we can then assign a name to each cluster if we'd like.

#### Cluster 1

In [ ]:
edinburgh_merged.loc[edinburgh_merged['Cluster Labels'] == 0, edinburgh_merged.columns[[1] + list(range(5, edinburgh_merged.shape[1]))]]

Latitude    Constituency       Rural/urban  \
0    55.9491  Edinburgh East  Large urban area   
18    55.948  Edinburgh East  Large urban area   
19   55.9485  Edinburgh East  Large urban area   
20    55.948  Edinburgh East  Large urban area   
21   55.9475  Edinburgh East  Large urban area   
22   55.9475  Edinburgh East  Large urban area   
23   55.9473  Edinburgh East  Large urban area   
24   55.9465  Edinburgh East  Large urban area   
25   55.9459  Edinburgh East  Large urban area   
26   55.9459  Edinburgh East  Large urban area   
27   55.9461  Edinburgh East  Large urban area   
28   55.9466  Edinburgh East  Large urban area   
29   55.9465  Edinburgh East  Large urban area   
34   55.9474  Edinburgh East  Large urban area   
35   55.9472  Edinburgh East  Large urban area   
39   55.9484  Edinburgh East  Large urban area   
41    55.948  Edinburgh East  Large urban area   
44   55.9479  Edinburgh East  Large urban area   
45   55.9482  Edinburgh East  Large urban area   
46   55.9481  Edinburgh East  Large urban area   
47   55.9477  Edinburgh East  Large urban area   
48   55.9479  Edinburgh East  Large urban area   
49   55.9479  Edinburgh East  Large urban area   
50   55.9479  Edinburgh East  Large urban area   
51   55.9479  Edinburgh East  Large urban area   
62   55.9501  Edinburgh East  Large urban area   
69   55.9498  Edinburgh East  Large urban area   
76   55.9499  Edinburgh East  Large urban area   
77   55.9499  Edinburgh East  Large urban area   
78     55.95  Edinburgh East  Large urban area   
79   55.9498  Edinburgh East  Large urban area   
80   55.9499  Edinburgh East  Large urban area   
98   55.9496  Edinburgh East  Large urban area   
100  55.9493  Edinburgh East  Large urban area   
128  55.9481  Edinburgh East  Large urban area   
132  55.9503  Edinburgh East  Large urban area   
142  55.9476  Edinburgh East  Large urban area   
165  55.9486  Edinburgh East  Large urban area   
166  55.9481  Edinburgh East  Large urban area   
167  55.9475  Edinburgh East  Large urban area   
168  55.9485  Edinburgh East  Large urban area   
169  55.9488  Edinburgh East  Large urban area   
170  55.9482  Edinburgh East  Large urban area   
171  55.9476  Edinburgh East  Large urban area   
172  55.9469  Edinburgh East  Large urban area   
173   55.947  Edinburgh East  Large urban area   
174  55.9471  Edinburgh East  Large urban area   
175  55.9466  Edinburgh East  Large urban area   
176  55.9466  Edinburgh East  Large urban area   
177  55.9471  Edinburgh East  Large urban area   
178  55.9468  Edinburgh East  Large urban area   
179  55.9468  Edinburgh East  Large urban area   
180  55.9465  Edinburgh East  Large urban area   
181  55.9486  Edinburgh East  Large urban area   
182   55.949  Edinburgh East  Large urban area   
183  55.9482  Edinburgh East  Large urban area   
184  55.9478  Edinburgh East  Large urban area   
185  55.9478  Edinburgh East  Large urban area   
186  55.9475  Edinburgh East  Large urban area   
187  55.9486  Edinburgh East  Large urban area   
188  55.9472  Edinburgh East  Large urban area   
189  55.9463  Edinburgh East  Large urban area   
190  55.9464  Edinburgh East  Large urban area   
193  55.9469  Edinburgh East  Large urban area   
194  55.9477  Edinburgh East  Large urban area   
195  55.9499  Edinburgh East  Large urban area   
196  55.9498  Edinburgh East  Large urban area   
197  55.9468  Edinburgh East  Large urban area   
198  55.9498  Edinburgh East  Large urban area   
199  55.9497  Edinburgh East  Large urban area   
200  55.9497  Edinburgh East  Large urban area   
201  55.9494  Edinburgh East  Large urban area   
202   55.949  Edinburgh East  Large urban area   
203  55.9489  Edinburgh East  Large urban area   
204  55.9488  Edinburgh East  Large urban area   
206   55.948  Edinburgh East  Large urban area   
207  55.9485  Edinburgh East  Large urban area   
208  55.9495  Edinburgh East  Large urban area   
209  55.9497  Edinburgh East  Large urban area   
210 

#### Cluster 2

In [ ]:
edinburgh_merged.loc[edinburgh_merged['Cluster Labels'] == 1, edinburgh_merged.columns[[1] + list(range(5, edinburgh_merged.shape[1]))]]

Latitude               Constituency       Rural/urban  \
241   55.957  Edinburgh North and Leith  Large urban area   
242  55.9548  Edinburgh North and Leith  Large urban area   
243  55.9575  Edinburgh North and Leith  Large urban area   
244  55.9568  Edinburgh North and Leith  Large urban area   
245  55.9562  Edinburgh North and Leith  Large urban area   
246  55.9569  Edinburgh North and Leith  Large urban area   
247   55.955  Edinburgh North and Leith  Large urban area   
248  55.9548  Edinburgh North and Leith  Large urban area   
250  55.9562  Edinburgh North and Leith  Large urban area   
251  55.9548  Edinburgh North and Leith  Large urban area   
252  55.9547  Edinburgh North and Leith  Large urban area   
253  55.9575  Edinburgh North and Leith  Large urban area   
255  55.9545  Edinburgh North and Leith  Large urban area   
259  55.9552  Edinburgh North and Leith  Large urban area   
260  55.9557  Edinburgh North and Leith  Large urban area   
261  55.9558  Edinburgh North and Leith  Large urban area   
263  55.9559  Edinburgh North and Leith  Large urban area   
264  55.9563  Edinburgh North and Leith  Large urban area   
266  55.9561  Edinburgh North and Leith  Large urban area   
267  55.9566  Edinburgh North and Leith  Large urban area   
268   55.957  Edinburgh North and Leith  Large urban area   
269  55.9564  Edinburgh North and Leith  Large urban area   
270   55.956  Edinburgh North and Leith  Large urban area   
271  55.9571  Edinburgh North and Leith  Large urban area   
272  55.9572  Edinburgh North and Leith  Large urban area   
273  55.9576  Edinburgh North and Leith  Large urban area   
274  55.9578  Edinburgh North and Leith  Large urban area   
275  55.9578  Edinburgh North and Leith  Large urban area   
276   55.958  Edinburgh North and Leith  Large urban area   
277  55.9584  Edinburgh North and Leith  Large urban area   
278  55.9581  Edinburgh North and Leith  Large urban area   
279  55.9578  Edinburgh North and Leith  Large urban area   
280  55.9576  Edinburgh North and Leith  Large urban area   
281  55.9587  Edinburgh North and Leith  Large urban area   
282  55.9583  Edinburgh North and Leith  Large urban area   
283   55.958  Edinburgh North and Leith  Large urban area   
284  55.9574  Edinburgh North and Leith  Large urban area   
285  55.9591  Edinburgh North and Leith  Large urban area   
286  55.9592  Edinburgh North and Leith  Large urban area   
287  55.9593  Edinburgh North and Leith  Large urban area   
288  55.9589  Edinburgh North and Leith  Large urban area   
289  55.9597  Edinburgh North and Leith  Large urban area   
290  55.9595  Edinburgh North and Leith  Large urban area   
291  55.9593  Edinburgh North and Leith  Large urban area   
292  55.9564  Edinburgh North and Leith  Large urban area   
294  55.9576  Edinburgh North and Leith  Large urban area   
296  55.9568  Edinburgh North and Leith  Large urban area   
297  55.9568  Edinburgh North and Leith  Large urban area   
298  55.9572  Edinburgh North and Leith  Large urban area   
299  55.9574  Edinburgh North and Leith  Large urban area   
300  55.9571  Edinburgh North and Leith  Large urban area   
301  55.9577  Edinburgh North and Leith  Large urban area   
302  55.9576  Edinburgh North and Leith  Large urban area   
303  55.9573  Edinburgh North and Leith  Large urban area   
304   55.958  Edinburgh North and Leith  Large urban area   
305  55.9572  Edinburgh North and Leith  Large urban area   
306  55.9581  Edinburgh North and Leith  Large urban area   
307  55.9584  Edinburgh North and Leith  Large urban area   
308  55.9584  Edinburgh North and Leith  Large urban area   
309  55.9586  Edinburgh North and Leith  Large urban area   
310  55.9589  Edinburgh North and Leith  Large urban area   
311  55.9591  Edinburgh North and Leith  Large urban area   
312   55.959  Edinburgh North and Leith  Large urban area   
313  55.9587  Edinburgh North and Leith  Large urban area   
314  55.9588  Edinburgh North and Leith

#### Cluster 3

In [ ]:
edinburgh_merged.loc[edinburgh_merged['Cluster Labels'] == 2, edinburgh_merged.columns[[1] + list(range(5, edinburgh_merged.shape[1]))]]

Latitude               Constituency       Rural/urban  \
1    55.9491             Edinburgh East  Large urban area   
2     55.952             Edinburgh East  Large urban area   
3     55.952             Edinburgh East  Large urban area   
4    55.9507             Edinburgh East  Large urban area   
5    55.9508             Edinburgh East  Large urban area   
6    55.9507             Edinburgh East  Large urban area   
7    55.9526             Edinburgh East  Large urban area   
8    55.9507             Edinburgh East  Large urban area   
9    55.9506             Edinburgh East  Large urban area   
10   55.9509             Edinburgh East  Large urban area   
11   55.9496             Edinburgh East  Large urban area   
12   55.9509             Edinburgh East  Large urban area   
13   55.9512             Edinburgh East  Large urban area   
14   55.9512             Edinburgh East  Large urban area   
15   55.9509             Edinburgh East  Large urban area   
16    55.951             Edinburgh East  Large urban area   
17   55.9509             Edinburgh East  Large urban area   
30   55.9485             Edinburgh East  Large urban area   
31   55.9489             Edinburgh East  Large urban area   
32   55.9482             Edinburgh East  Large urban area   
33    55.948             Edinburgh East  Large urban area   
36   55.9483             Edinburgh East  Large urban area   
37   55.9485             Edinburgh East  Large urban area   
38   55.9488             Edinburgh East  Large urban area   
40   55.9486             Edinburgh East  Large urban area   
42   55.9484             Edinburgh East  Large urban area   
43   55.9484             Edinburgh East  Large urban area   
52   55.9493             Edinburgh East  Large urban area   
53   55.9489             Edinburgh East  Large urban area   
54   55.9477             Edinburgh East  Large urban area   
55   55.9481             Edinburgh East  Large urban area   
56   55.9482             Edinburgh East  Large urban area   
57   55.9502             Edinburgh East  Large urban area   
58   55.9488             Edinburgh East  Large urban area   
59    55.949             Edinburgh East  Large urban area   
60    55.949             Edinburgh East  Large urban area   
61   55.9497             Edinburgh East  Large urban area   
63   55.9493             Edinburgh East  Large urban area   
64   55.9497             Edinburgh East  Large urban area   
65   55.9484             Edinburgh East  Large urban area   
66   55.9488             Edinburgh East  Large urban area   
67   55.9484             Edinburgh East  Large urban area   
68   55.9497             Edinburgh East  Large urban area   
70   55.9505             Edinburgh East  Large urban area   
71   55.9505             Edinburgh East  Large urban area   
72   55.9503             Edinburgh East  Large urban area   
73   55.9502             Edinburgh East  Large urban area   
74   55.9501             Edinburgh East  Large urban area   
75   55.9504             Edinburgh East  Large urban area   
81   55.9504             Edinburgh East  Large urban area   
82   55.9503             Edinburgh East  Large urban area   
83   55.9502             Edinburgh East  Large urban area   
84   55.9512             Edinburgh East  Large urban area   
85   55.9509             Edinburgh East  Large urban area   
86   55.9506             Edinburgh East  Large urban area   
87   55.9505             Edinburgh East  Large urban area   
88   55.9498             Edinburgh East  Large urban area   
89   55.9491             Edinburgh East  Large urban area   
90   55.9498             Edinburgh East  Large urban area   
91   55.9497             Edinburgh East  Large urban area   
92   55.9498             Edinburgh East  Large urban area   
93   55.9496             Edinburgh East  Large urban area   
94   55.9497             Edinburgh East  Large urban area   
95   55.9493             Edinburgh East  Large urban area   
96   55.9492             Edinburgh East

#### Cluster 4

In [ ]:
edinburgh_merged.loc[edinburgh_merged['Cluster Labels'] == 3, edinburgh_merged.columns[[1] + list(range(5, edinburgh_merged.shape[1]))]]

Latitude    Constituency       Rural/urban Lower layer super output area  \
106  55.9432  Edinburgh West  Large urban area            Deans Village - 07   
127  55.9432  Edinburgh West  Large urban area            Deans Village - 07   
237  55.9432  Edinburgh West  Large urban area            Deans Village - 07   
238  55.9432  Edinburgh West  Large urban area            Deans Village - 07   
239  55.9432  Edinburgh West  Large urban area            Deans Village - 07   
319  55.9432  Edinburgh West  Large urban area            Deans Village - 07   
322  55.9432  Edinburgh West  Large urban area            Deans Village - 07   
323  55.9432  Edinburgh West  Large urban area            Deans Village - 07   
324  55.9432  Edinburgh West  Large urban area            Deans Village - 07   

    Middle layer super output area  Cluster Labels 1st Most Common Venue  \
106                  Deans Village               3                 Hotel   
127                  Deans Village               3                 Hotel   
237                  Deans Village               3                 Hotel   
238                  Deans Village               3                 Hotel   
239                  Deans Village               3                 Hotel   
319                  Deans Village               3                 Hotel   
322                  Deans Village               3                 Hotel   
323                  Deans Village               3                 Hotel   
324                  Deans Village               3                 Hotel   

    2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
106         Grocery Store                   Pub         Rugby Stadium   
127         Grocery Store                   Pub         Rugby Stadium   
237         Grocery Store                   Pub         Rugby Stadium   
238         Grocery Store                   Pub         Rugby Stadium   
239         Grocery Store                   Pub         Rugby Stadium   
319         Grocery Store                   Pub         Rugby Stadium   
322         Grocery Store                   Pub         Rugby Stadium   
323         Grocery Store                   Pub         Rugby Stadium   
324         Grocery Store                   Pub         Rugby Stadium   

    5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
106            Sports Bar         Bowling Green           Auto Garage   
127            Sports Bar         Bowling Green           Auto Garage   
237            Sports Bar         Bowling Green           Auto Garage   
238            Sports Bar         Bowling Green           Auto Garage   
239            Sports Bar         Bowling Green           Auto Garage   
319            Sports Bar         Bowling Green           Auto Garage   
322            Sports Bar         Bowling Green           Auto Garage   
323            Sports Bar         Bowling Green           Auto Garage   
324            Sports Bar         Bowling Green           Auto Garage   

    8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
106        Soccer Stadium                 Trail           Tram Station  
127        Soccer Stadium                 Trail           Tram Station  
237        Soccer Stadium                 Trail           Tram Station  
238        Soccer Stadium                 Trail           Tram Station  
239        Soccer Stadium                 Trail           Tram Station  
319        Soccer Stadium                 Trail           Tram Station  
322        Soccer Stadium                 Trail           Tram Station  
323        Soccer Stadium                 Trail           Tram Station  
324        Soccer Stadium                 Trail           Tram Station

#### Cluster 5

In [ ]:
edinburgh_merged.loc[edinburgh_merged['Cluster Labels'] == 4, edinburgh_merged.columns[[1] + list(range(5, edinburgh_merged.shape[1]))]]

Latitude          Constituency       Rural/urban  \
133  55.9493  Edinburgh South West  Large urban area   
134  55.9496  Edinburgh South West  Large urban area   
135  55.9499  Edinburgh South West  Large urban area   
136  55.9495  Edinburgh South West  Large urban area   
137  55.9472        Edinburgh East  Large urban area   
138  55.9472        Edinburgh East  Large urban area   
139  55.9491  Edinburgh South West  Large urban area   
140  55.9471        Edinburgh East  Large urban area   
141  55.9486  Edinburgh South West  Large urban area   
143  55.9487  Edinburgh South West  Large urban area   
144  55.9483  Edinburgh South West  Large urban area   
145  55.9482  Edinburgh South West  Large urban area   
146  55.9482  Edinburgh South West  Large urban area   
147   55.949  Edinburgh South West  Large urban area   
148  55.9489  Edinburgh South West  Large urban area   
149  55.9476        Edinburgh East  Large urban area   
150  55.9485  Edinburgh South West  Large urban area   
151  55.9479        Edinburgh East  Large urban area   
152  55.9485        Edinburgh East  Large urban area   
153  55.9479        Edinburgh East  Large urban area   
154  55.9474        Edinburgh East  Large urban area   
155  55.9475        Edinburgh East  Large urban area   
156  55.9476        Edinburgh East  Large urban area   
157  55.9471        Edinburgh East  Large urban area   
158  55.9476        Edinburgh East  Large urban area   
159   55.949        Edinburgh East  Large urban area   
160   55.947        Edinburgh East  Large urban area   
161  55.9473        Edinburgh East  Large urban area   
162  55.9476        Edinburgh East  Large urban area   
163  55.9491        Edinburgh East  Large urban area   
164   55.948        Edinburgh East  Large urban area   
191  55.9462        Edinburgh East  Large urban area   
192  55.9462        Edinburgh East  Large urban area   
205   55.949        Edinburgh East  Large urban area   
233  55.9492  Edinburgh South West  Large urban area   
240   55.949        Edinburgh East  Large urban area   

                      Lower layer super output area  \
133                                  Tollcross - 02   
134                                  Tollcross - 02   
135                                  Tollcross - 02   
136                                  Tollcross - 02   
137  Old Town, Princes Street and Leith Street - 02   
138  Old Town, Princes Street and Leith Street - 02   
139                                  Tollcross - 02   
140  Old Town, Princes Street and Leith Street - 02   
141                                  Tollcross - 02   
143                                  Tollcross - 02   
144                                  Tollcross - 02   
145                                  Tollcross - 02   
146                                  Tollcross - 02   
147                                  Tollcross - 02   
148                                  Tollcross - 02   
149                                  Tollcross - 02   
150                                  Tollcross - 02   
151                                  Tollcross - 02   
152                                  Tollcross - 02   
153                                  Tollcross - 02   
154                                  Tollcross - 02   
155                                  Tollcross - 02   
156                                  Tollcross - 02   
157                                  Tollcross - 02   
158                                  Tollcross - 02   
159                                  Tollcross - 02   
160                                  Tollcross - 02   
161                                  Tollcross - 02   
162                                  Tollcross - 02   
163                                  Tollcross - 02   
164                                  Tollcross - 02   
191                                  Tollcross - 03   
192                                  Tollcross - 03   
205  Old Town, Princes Street and Leith Street - 02   
233   